In [3]:
#Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [4]:
#Check Your ZIP File Name
import os
os.listdir("/content/drive/MyDrive")


['Colab Notebooks',
 'Hunar Intern',
 'ANPR_PROJECT',
 'ANPRDATASET1.zip',
 'ATCC_DATASET1.zip',
 'ATCC',
 'ANPR']

In [5]:
#Unzip Your ANPR Dataset
!unzip "/content/drive/MyDrive/ANPRDATASET1.zip" -d "/content/anpr_dataset"


Streaming output truncated to the last 5000 lines.
  inflating: /content/anpr_dataset/labels/train/xemay1968_jpg.rf.166105631e9a5ca05841aec083702e9b.txt  
  inflating: /content/anpr_dataset/labels/train/xemay1968_jpg.rf.36f5e6ab6560a8e1f7800ce3316f219d.txt  
  inflating: /content/anpr_dataset/labels/train/xemay1968_jpg.rf.c44d173cdb9b78e972e17ff9aaee97b0.txt  
  inflating: /content/anpr_dataset/labels/train/xemay1969_jpg.rf.04f15eaf4d601a68a0a3a7665a897ac1.txt  
  inflating: /content/anpr_dataset/labels/train/xemay196_jpg.rf.5311c8fa681e9a856039033f437bbbee.txt  
  inflating: /content/anpr_dataset/labels/train/xemay196_jpg.rf.aea4333b126488fe840977a6d304f0be.txt  
  inflating: /content/anpr_dataset/labels/train/xemay196_jpg.rf.e49ab47445d4947b691add3abe535121.txt  
  inflating: /content/anpr_dataset/labels/train/xemay1970_jpg.rf.25f0172f5c4d7d536158b7987857501e.txt  
  inflating: /content/anpr_dataset/labels/train/xemay1970_jpg.rf.299cd97da511ae3b8f632aff15ef2037.txt  
  inflating: /co

In [6]:
#Install Required Libraries
!pip install -q ultralytics easyocr opencv-python pandas tqdm


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 67.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.9/2.9 MB 114.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 180.7/180.7 kB 21.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 978.2/978.2 kB 49.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 300.6/300.6 kB 32.5 MB/s eta 0:00:00


In [7]:
#Load YOLO Model
from ultralytics import YOLO
model = YOLO("yolov8n.pt")


Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


In [8]:
#Setup Output Folders in Drive
import os

BASE_OUT  = "/content/drive/MyDrive/ANPR"
IMAGE_OUT = f"{BASE_OUT}/plates"
CSV_PATH  = f"{BASE_OUT}/anpr_results.csv"

os.makedirs(IMAGE_OUT, exist_ok=True)
print("✅ Output folders created")


✅ Output folders created


In [9]:
#Load OCR Engine
import easyocr
reader = easyocr.Reader(['en'])


Progress: |██████████████████████████████████████████████████| 100.0% Complete

Progress: |██████████████████████████████████████████████████| 100.0% Complete

In [10]:
#Run ANPR (Plate Detection + OCR + CSV)

import cv2
import pandas as pd
from tqdm import tqdm
import os
import easyocr # Added import

reader = easyocr.Reader(['en']) # Added initialization

dataset_dir = "/content/anpr_dataset"

results = []

image_files = []
for root, _, files in os.walk(dataset_dir):
    for f in files:
        if f.lower().endswith((".jpg", ".png", ".jpeg")):
            image_files.append(os.path.join(root, f))

print("Total images found:", len(image_files))

for img_path in tqdm(image_files):
    img = cv2.imread(img_path)
    if img is None:
        continue

    detections = model(img)[0]

    for i, box in enumerate(detections.boxes):
        cls = int(box.cls)
        name = detections.names[cls]

        if name in ["car", "truck", "bus", "motorcycle"]:
            x1, y1, x2, y2 = map(int, box.xyxy[0])
            crop = img[y1:y2, x1:x2]

            if crop.size == 0:
                continue

            ocr_result = reader.readtext(crop)
            plate_text = ocr_result[0][-2] if ocr_result else "N/A"

            save_path = os.path.join(IMAGE_OUT, os.path.basename(img_path))
            cv2.imwrite(save_path, crop)

            results.append({
                "image": os.path.basename(img_path),
                "vehicle_type": name,
                "plate_text": plate_text
            })

df = pd.DataFrame(results)
df.to_csv(CSV_PATH, index=False)
df.head()


Total images found: 26929


  0%|          | 0/26929 [00:00<?, ?it/s]


0: 640x640 (no detections), 7.8ms
Speed: 13.2ms preprocess, 7.8ms inference, 6.5ms postprocess per image at shape (1, 3, 640, 640)


  0%|          | 1/26929 [00:01<11:40:06,  1.56s/it]


0: 640x640 (no detections), 7.7ms
Speed: 3.1ms preprocess, 7.7ms inference, 0.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 7.8ms
Speed: 3.7ms preprocess, 7.8ms inference, 0.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 7.7ms
Speed: 2.8ms preprocess, 7.7ms inference, 0.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 person, 7.8ms
Speed: 3.0ms preprocess, 7.8ms inference, 37.7ms postprocess per image at shape (1, 3, 640, 640)


...


0: 576x640 1 person, 3 cars, 1 truck, 8.9ms
Speed: 5.8ms preprocess, 8.9ms inference, 1.6ms postprocess per image at shape (1, 3, 576, 640)


100%|█████████▉| 26928/26929 [1:53:53<00:00,  3.40it/s]


0: 448x640 3 cars, 9.2ms
Speed: 3.3ms preprocess, 9.2ms inference, 1.6ms postprocess per image at shape (1, 3, 448, 640)


100%|██████████| 26929/26929 [1:53:53<00:00,  3.94it/s]


image vehicle_type plate_text
0                               4a907dd7abf4d097.jpg          car    2219e59
1                               4a907dd7abf4d097.jpg          car    2219es9
2                               4a907dd7abf4d097.jpg          car        N/A
3                               4a907dd7abf4d097.jpg          car        N/A
4  Cars234_png_jpg.rf.91842192d7526760bbf35e6883c...          car   IM4U 555

In [11]:
#Download CSV to Your System
from google.colab import files
files.download(CSV_PATH)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>